## NYC Taxi Dataset Python API Example
This is a simple example 
- To connect to a GPUDB
- To Use the GPUDB Object to retrieve 10 records
- Use the GPUDB record to get specific columns
- Apply Filter to the colums
- Apply GroupBy clause

The complete Python API reference can be found in - https://www.kinetica.com/docs/api/python/source/gpudb.html

As the first step we import all the necessary packages

In [ ]:
import gpudb #This is the Kinetica GPUDB Package"
import collections
import time
import json


- Next we create a connection to the Kinetica Server
- In the below example please update the host ip address with your server IP or name 
- or 'localhost' if you are running jupyter on the same node as the Kinetica Server
- The default port is 9191.

In [ ]:
""" Establish connection with a locally-running instance of Kinetica, using binary encoding to save memory """
h_db = gpudb.GPUdb(encoding='BINARY', host='172.16.81.133', port='9191')


In the next section we take the GPUDB object and we try and get 10 rows from the data set. This is similar to executing, 
- <b>select * from nyctaxi limit 10</b>

- We use the <b>get_records()</b> function. <b>get_records()</b> function returns a json with other metadata along with the data.
- We select "records_json" element where the action records are embedded. 
- We hold it in a variable nyctaxiresponse


In [ ]:
nyctaxiresponse = h_db.get_records(table_name="nyctaxi", offset=0, limit=10, encoding="json")['records_json']
print (nyctaxiresponse)

In [ ]:
table = gpudb.GPUdbTable(None, 'nyctaxi', db=h_db)
for r in table.get_records(limit=1):
     print(r)

Next we are interested in the "fare_amount". We extract that into an python list.

In [ ]:
fare_amount = []

print ("{:<15s} {:<20s}".format("passenger_count","fare_amount"))
print ("{:-<15s} {:-<20s}".format("",""))
for nyctaxi_record in nyctaxiresponse:
    json_record = json.loads(nyctaxi_record)
    fare_amount.append(json_record["fare_amount"])  
    print ("{passenger_count:<15d}  ${fare_amount:<10.2f} ".format(**json_record))
   


In the next step we are going to work with to get sepcific columns from the table. In this example we get the passenger_count, fare_amount and the trip_distance.

- Add the following expression to the options={"expression":"passenger_count=1"}
- This will limit the records to taxi rides with single passengers


In [ ]:
results = h_db.get_records_by_column(table_name="nyctaxi", 
                                     column_names=["passenger_count","fare_amount","trip_distance"],
                                     offset=0, limit=10, encoding="json", options={})['json_encoded_response']
print(results)

### Trip counts and Fare Amount by Vendor ID

In [ ]:
result_json1 = h_db.aggregate_group_by(table_name="nyctaxi", 
                                       column_names=["vendor_id", 'count(*)', 'sum(fare_amount) as Total_Fare'],
                                       offset=0, limit=10, encoding="json", options={ "sort_order":"descending", "sort_by":"value"})['json_encoded_response']
print (result_json1)

### Dynamic Schema

The response from Kinetica is formatted depending on the request and the data being returned. This is known as a dynamic schema. The response will contain an Avro schema string (in the response_schema_str field) and then either an Avro binary encoded response (in the binary_encoded_response field) or an Avro JSON encoded response (in the json_encoded_response field). 

For dynamic schema responses, the response always consists of a series of arrays of various types, corresponding to the columns being returned. These arrays are labeled column_1, column_2, etc. In addition there is a string array column named column_headers containing the names or aliases of the returned columns. The first name in column_headers corresponds to column_1, the second to column_2 and so on. Lastly, there is a string array column named column_datatypes containing the data types of the returned columns. These correspond to the returned data columns in the same way column_headers do.

In the following cell we parse the dynamic scheme to print the values corresponding to the Headers

In [ ]:
result_json = json.loads(result_json1)
#print (result_json)
count = 0
colum_dic = dict()
for i in  result_json["column_headers"]:
    count +=1
    column_number = "column_" + str(count)
    print (i)
    print (result_json[column_number])
    colum_dic[i] = result_json[column_number]



### Average Fare by Passenger Count
- The records are limited to 10

In [ ]:
h_db.aggregate_group_by(table_name="nyctaxi", 
                                       column_names=["passenger_count",  'avg(total_amount) as Total_Fare'],
                                       offset=0, limit=1000, encoding="json", options={ "sort_order":"ascending", "sort_by":"value"})['json_encoded_response']

### Number of trips by Passenger Count and Year
- The records are limited to 10

In [ ]:
h_db.aggregate_group_by(table_name="nyctaxi", 
                                       column_names=["YEAR(pickup_datetime) AS Pickup_Year", "passenger_count AS Total_Passengers", "count(*) as Total_Trips"],
                                       offset=0, limit=10, encoding="json", options={ "sort_order":"ascending", "sort_by":"value"})['json_encoded_response']

### Number of trips by Year, trip distance and passenger_count

- The records are limited to 10


In [ ]:
h_db.aggregate_group_by(table_name="nyctaxi", 
                                       column_names=["YEAR(pickup_datetime) AS Pickup_Year", "trip_distance AS Trip_Distance", "passenger_count AS Total_Passengers", "count(*) as Total_Trips"],
                                       offset=0, limit=10, encoding="json", options={ "sort_order":"ascending", "sort_by":"value"})['json_encoded_response']

### Statistics for Fare Amount
 - Count, Mean, Standard Deviation, Variance and Skew

In [ ]:
h_db.aggregate_statistics(table_name="nyctaxi", 
                                       column_name="fare_amount",
                                      stats = "count, mean, stdv, variance, skew",
                                         options={})['stats']

### Conclusion

This is was just a brief introduction to the Python API. The advantage of using Python API is that you can use the results to chart and map the graphs, and use other python packages to serve the data back to other applications.